### W231: Eviction Notices

In [65]:
from __future__ import division
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import folium
from folium.plugins import MarkerCluster
%matplotlib inline

In [158]:
evictions = pd.read_csv('Eviction_Notices.csv', index_col=0)

In [159]:
evictions.head()

Address           City State    Zip  \
Eviction_ID                                                              
M153486         0 Block of Raymond  Avenue  San Francisco    CA  94134   
M153490       2700 Block of Folsom  Street  San Francisco    CA  94110   
M153487       300 Block of San Benito  Way  San Francisco    CA  94127   
M153438        100 Block of Elmira  Street  San Francisco    CA  94124   
M153488      0 Block of Morningside  Drive  San Francisco    CA  94132   

              File Date Non Payment Breach Nuisance Illegal Use  \
Eviction_ID                                                       
M153486      12/30/2015       False  False    False       False   
M153490      12/30/2015       False   True    False       False   
M153487      12/30/2015       False  False     True       False   
M153438      12/30/2015       False  False    False       False   
M153488      12/30/2015        True  False    False       False   

            Failure to Sign Renewal                  ...                    \
Eviction_ID                                          ...                     
M153486                       False                  ...                     
M153490                       False                  ...                     
M153487                       False                  ...                     
M153438                       False                  ...                     
M153488                       False                  ...                     

            Other Cause Late Payments Lead Remediation Development  \
Eviction_ID                                                          
M153486           False         False            False       False   
M153490           False         False            False       False   
M153487           False         False            False       False   
M153438           False         False            False       False   
M153488           False         False            False       False   

            Good Samaritan Ends Constraints Constraints Date  \
Eviction_ID                                                    
M153486                     NaN       False              NaN   
M153490                     NaN       False              NaN   
M153487                     NaN       False              NaN   
M153438                     NaN       False       02/26/2021   
M153488                     NaN       False              NaN   

            Supervisor_District           Neighborhood  \
Eviction_ID                                              
M153486                      10      Visitacion Valley   
M153490                       9                Mission   
M153487                       7     West of Twin Peaks   
M153438                      10  Bayview Hunters Point   
M153488                       7        Sunset/Parkside   

                                   Client_Location  
Eviction_ID                                         
M153486      (37.7121484523486, -122.404287840075)  
M153490       (37.7532984475532, -122.41422876374)  
M153487      (37.7296676394739, -122.467418596281)  
M153438       (37.7353069212531, -122.40373356189)  
M153488      (37.7331813515864, -122.492299907103)  

[5 rows x 29 columns]

### Data cleaning

In [160]:
# Fix dates
evictions['File Date'] = pd.to_datetime(evictions['File Date'])

In [162]:
# Extract latitude, longitude
evictions = evictions.replace('1 QNAN\n', np.nan)
evictions['latitude'] = evictions['Client_Location'].str.strip('()').str.split(', ').str.get(0).astype(float)
evictions['longitude'] = evictions['Client_Location'].str.strip('()').str.split(', ').str.get(1).astype(float)
# Filter out null location values
evictions = evictions[evictions['longitude'].notnull()]

### Get tuples that don't contain "Block"

In [163]:
noblock = evictions[~evictions['Address'].str.contains('Block')]

In [164]:
len(noblock)

468

In [60]:
# Notice the invalid location coordinates

In [165]:
noblock.head(5)

Address           City State    Zip  File Date  \
Eviction_ID                                                            
M142533      1950 Cabrillo St  San Francisco    CA  94121 2014-11-13   
M142503       626 OFARRELL ST  San Francisco    CA  94109 2014-11-07   
M141919       601 OFARRELL ST  San Francisco    CA  94109 2014-08-29   
M141654       540 OFARRELL ST  San Francisco    CA  94102 2014-07-23   
M140619       835 OFARRELL ST  San Francisco    CA  94109 2014-03-31   

            Non Payment Breach Nuisance Illegal Use Failure to Sign Renewal  \
Eviction_ID                                                                   
M142533           False  False    False       False                   False   
M142503           False   True    False       False                   False   
M141919           False  False    False        True                   False   
M141654           False   True    False       False                   False   
M140619           False   True    False       False                   False   

                  ...       Lead Remediation Development Good Samaritan Ends  \
Eviction_ID       ...                                                          
M142533           ...                  False       False                 NaN   
M142503           ...                  False       False                 NaN   
M141919           ...                  False       False                 NaN   
M141654           ...                  False       False                 NaN   
M140619           ...                  False       False                 NaN   

            Constraints Constraints Date Supervisor_District Neighborhood  \
Eviction_ID                                                                 
M142533           False              NaN                 NaN          NaN   
M142503           False              NaN                 NaN          NaN   
M141919           False              NaN                 NaN          NaN   
M141654           False              NaN                 NaN          NaN   
M140619           False              NaN                 NaN          NaN   

                                  Client_Location        latitude  \
Eviction_ID                                                         
M142533      (2110602.45058652, 5989586.36513565)  2110602.450587   
M142503      (2114160.50189096, 6008204.46476792)  2114160.501891   
M141919       (2114141.93171825, 6008363.0565909)  2114141.931718   
M141654      (2114222.41688431, 6008654.76139783)  2114222.416884   
M140619      (2113985.42382983, 6007230.84642008)  2113985.423830   

                  longitude  
Eviction_ID                  
M142533      5989586.365136  
M142503      6008204.464768  
M141919      6008363.056591  
M141654      6008654.761398  
M140619      6007230.846420  

[5 rows x 31 columns]

#### Get coordinates from the street address field

In [95]:
from geopy.geocoders import Nominatim
geolocator = Nominatim(timeout=10)

In [120]:
# Get coordinates
for index, row in noblock.iterrows():
    address = ', '.join([row['Address'], 'San Francisco'])    
    # Modify dataframe
    try:
        location = geolocator.geocode(address)
        noblock.loc[index, 'latitude'] = location.latitude
        noblock.loc[index, 'longitude'] = location.longitude
        
    # Pass if coordinates not available
    except:
        pass

#### Only look at problem evictions

In [172]:
problem_noblock = noblock[noblock['Non Payment'] | noblock['Breach'] | noblock['Breach'] | 
                          noblock['Nuisance'] | noblock['Illegal Use'] | noblock['Late Payments'] ]

In [173]:
len(problem_noblock)

313

Map these notices

In [147]:
def show_map(df):
    SF_COORDINATES = (37.78, -122.45)
    # Create map
    tiles = r'https://api.mapbox.com/v4/mapbox.streets/{z}/{x}/{y}.png?access_token=pk.eyJ1Ijoia29ubmlhbWNoYW4iLCJhIjoiY2loZjZ1aDB4MGxxaHR0bHpmMDRrczNubCJ9.42XTV2wAGebwq8n5KvJBxQ'
    attr = '© Mapbox, © OpenStreetMap'
    eviction_map = folium.Map(location=SF_COORDINATES, tiles=tiles, zoom_start=13, attr=attr)
    
    # Cluster
#     notices = zip(df['latitude'], df['longitude'])
#     eviction_map.add_children(MarkerCluster(locations=notices,
#                                             popups=df.index))
    # Individual markers
    for index, row in df.iterrows():
        popup = index + ' ('+ row['Address'] + ')'
        folium.CircleMarker(location=(row['latitude'], row['longitude']),
                            radius=3, popup=popup).add_to(eviction_map)
    return eviction_map

In [149]:
show_map(problem_noblock)

Candidate: M101768 (please see Google doc for detail explanation)

In [174]:
problem_noblock.loc['M101768', :]

Address                                            462 33rd Ave
City                                              San Francisco
State                                                        CA
Zip                                                       94122
File Date                                   2010-12-06 00:00:00
Non Payment                                               False
Breach                                                     True
Nuisance                                                  False
Illegal Use                                               False
Failure to Sign Renewal                                   False
Access Denial                                             False
Unapproved Subtenant                                      False
Owner Move In                                             False
Demolition                                                False
Capital Improvement                                       False
Substantial Rehab                       

### Filter dates after 2010

In [175]:
evictions = evictions[evictions['File Date'].dt.year >= 2010]

### Evictions with Late Payments

In [176]:
problem_evictions = evictions[evictions['Non Payment'] | evictions['Breach'] | evictions['Breach'] | 
                          evictions['Nuisance'] | evictions['Illegal Use'] | evictions['Late Payments'] ]

In [177]:
len(problem_evictions)

6286

In [156]:
# Export
problem_evictions.to_csv('problem_evictions.csv')

In [157]:
show_map(problem_evictions)